# Read all Instructions

## Technical Skills Evaluation for Bioinformatics Scientist position

The goal of this notebook is to assess several sets of skills that will be used on a regular basis in this position at Novonesis.

**Instructions:**
* Complete all sections below. All commands used must be documented in this notebook.
* If you do not know an answer to a question, please use relevant resources to complete all sections to the best of your ability.
* If you cannot answer a question, explain your thought processes and what subsequent steps you would take in the future to answer the question.
* If you use outside resources please cite them as necessary (_i.e._ anything copy and pasted needs a citation including Stack Overflow).
* Questions requiring anything other than python code should be included as markdown cells with proper formatting (Code should be formatted as code, links should contain text with a hyperlink).

## Sequence data manipulation
The Bioinformatics Scientist will work heavily with sequence data. This section is intended to evaluate your familiarity with sequence data manipulation. 


1. Download the Agaricus bisporus genome sequence as a Genbank file (gbff) from NCBI. You can find it [here](https://www.ncbi.nlm.nih.gov/datasets/genome/GCA_000300575.2/).

2. Calculate the length of each sequence record (_i.e._ contig), and print out each contig ID and its corresponding length such that each line is a single contig ID and its length separated by a single tab. 

3. Extract all CDS features that have translations, and write the translations to a new multi-fasta file where the fasta header for each CDS is the locus_tag.

4. For each protein sequence you extracted in step 3, calculate counts for each amino acid.

5. Provide the command you would use to create a blast database from your multi-fasta protein file.

6. Illumina sequencing: describe the output data format, and provide a general overview of processing and QC of Illumina genomic sequence data. Provide an example command for quality and adapter trimming using a program of your choice. 

7. Nanopore sequencing: describe the output data format, and provide a general overview of processing and QC of Nanopore genomic sequence data. Provide an example command for quality and adapter trimming using a program of your choice. 

8. You have PE sequence reads from 2 runs of Illumina sequencing, run1_R1.fastq.gz and run1_R2.fastq.gz are the R1 and R2 files from run 1, and run2_R1.fastq.gz and run2_R2.fastq.gz are the R1 and R2 files from run 2. Provide a command below that would pool the data from these two runs into single R1 and R2 files. 

9. Please provide a command to randomly subsample 10,000 reads from your pooled dataset in question 8.

## Q1 

Downloaded the genbank (gbff) file from - https://www.ncbi.nlm.nih.gov/datasets/genome/GCF_000300575.1/

In [1]:
# Q2
from Bio import SeqIO

# Path to the GenBank file
gbff_file = "/Users/shatakshishewale/Desktop/ncbi_dataset/ncbi_dataset/data/GCA_000300575.1/genomic.gbff"

# Parse and print contig ID and length respectively
for record in SeqIO.parse(gbff_file, "genbank"):
    print(f"{record.id} \t {len(record.seq)}")
    
# Reference - Biopython Tutorial and Cookbook – Section on parsing GenBank files  
# https://biopython.org/docs/1.84/Tutorial/chapter_seqio.html#reading-sequence-files

JH931605.1 	 3343696
JH931606.1 	 3111184
JH931607.1 	 2553239
JH931608.1 	 2387012
JH931609.1 	 2368395
JH931610.1 	 2334609
JH931611.1 	 2081940
JH931612.1 	 1953713
JH931613.1 	 1748887
JH931614.1 	 1635119
JH931615.1 	 1336043
JH931616.1 	 1144839
JH931617.1 	 1061846
JH931618.1 	 877174
JH931619.1 	 626669
JH931620.1 	 613464
JH931621.1 	 531765
JH931622.1 	 249292
JH931623.1 	 197385
JH931624.1 	 24809
JH931625.1 	 14553
JH931626.1 	 7624
JH931627.1 	 5831
JH931628.1 	 5606
JH931629.1 	 4528
JH931630.1 	 4408
JH931631.1 	 4107
JH931632.1 	 3428
JH931633.1 	 2580


In [2]:
# Q3

from Bio import SeqIO
from Bio.Seq import Seq
from Bio.SeqRecord import SeqRecord

# Path to the GenBank file
gbff_file = "/Users/shatakshishewale/Desktop/ncbi_dataset/ncbi_dataset/data/GCA_000300575.1/genomic.gbff"

# Output file where translated CDS proteins will be written in FASTA format
output_fasta = "/Users/shatakshishewale/Desktop/ncbi_dataset/ncbi_dataset/data/GCA_000300575.1/cds_translations.fasta"

# List to hold all valid CDS records that meet the conditions
cds_records = []

# Loop through each sequence record (i.e., contig) in the GenBank file
for record in SeqIO.parse(gbff_file, "genbank"):
    
    # Loop through each feature in the sequence record
    for feature in record.features:
        
        # Only process features of type "CDS" (coding sequences)
        if feature.type == "CDS":
            
            # Ensure the CDS has both a protein translation and a locus_tag
            if "translation" in feature.qualifiers and "locus_tag" in feature.qualifiers:
                
                # Extract the amino acid sequence and the locus tag
                aa_seq = feature.qualifiers["translation"][0]
                locus = feature.qualifiers["locus_tag"][0]
                
                # Create a SeqRecord for this CDS and append it to the list
                cds_record = SeqRecord(Seq(aa_seq), id=locus, description="")
                cds_records.append(cds_record)

# Write all the CDS records with translations to a multi-FASTA file
num_written = SeqIO.write(cds_records, output_fasta, "fasta")

# Print confirmation message with output details
print(f"{num_written} CDS protein sequences were written to:")
print(output_fasta)


# Reference -  Biopython Tutorial and Cookbook (Bio.SeqFeature module) and Stack Overflow
# https://biopython.org/docs/1.76/api/Bio.SeqFeature.html
# https://www.biostars.org/p/9542737/

10448 CDS protein sequences were written to:
/Users/shatakshishewale/Desktop/ncbi_dataset/ncbi_dataset/data/GCA_000300575.1/cds_translations.fasta


In [3]:
# Q4

from collections import Counter
from Bio import SeqIO

# Input file from step 3
fasta_file = "/Users/shatakshishewale/Desktop/ncbi_dataset/ncbi_dataset/data/GCA_000300575.1/cds_translations.fasta"

# Loop through each protein sequence
for record in SeqIO.parse(fasta_file, "fasta"):
    protein_id = record.id
    sequence = record.seq
    
    # Count amino acids
    aa_counts = Counter(sequence)
    
    # Print the result
    print(f"Amino acid counts for {protein_id}:")
    for aa, count in sorted(aa_counts.items()):
        print(f"{aa}: {count}")
    print("-" * 40)

# Reference -  Biopython Tutorial and Cookbook (Counter Objects) and Stack Overflow
# https://docs.python.org/3/library/collections.html#collections.Counter
# https://stackoverflow.com/questions/14397504/how-to-count-amino-acids-in-fasta-formated-file

Amino acid counts for AGABI2DRAFT_189137:
A: 5
C: 5
D: 5
E: 3
F: 5
G: 3
H: 4
I: 2
K: 1
L: 7
M: 3
N: 2
P: 4
Q: 2
R: 5
S: 6
T: 6
V: 3
W: 1
Y: 3
----------------------------------------
Amino acid counts for AGABI2DRAFT_175561:
A: 70
C: 8
D: 79
E: 106
F: 42
G: 55
H: 16
I: 60
K: 95
L: 104
M: 28
N: 33
P: 41
Q: 56
R: 75
S: 72
T: 54
V: 53
W: 10
Y: 37
----------------------------------------
Amino acid counts for AGABI2DRAFT_113535:
A: 53
C: 8
D: 31
E: 20
F: 21
G: 42
H: 18
I: 36
K: 20
L: 61
M: 12
N: 27
P: 31
Q: 21
R: 27
S: 51
T: 40
V: 39
W: 14
Y: 17
----------------------------------------
Amino acid counts for AGABI2DRAFT_62215:
A: 6
D: 7
E: 8
F: 3
G: 17
H: 1
I: 2
K: 11
L: 5
M: 3
N: 7
P: 3
Q: 8
R: 1
S: 5
T: 4
V: 4
Y: 1
----------------------------------------
Amino acid counts for AGABI2DRAFT_189140:
A: 49
C: 3
D: 44
E: 39
F: 24
G: 49
H: 18
I: 27
K: 46
L: 37
M: 17
N: 20
P: 18
Q: 12
R: 21
S: 22
T: 27
V: 43
W: 4
Y: 13
----------------------------------------
Amino acid counts for AGABI2DRAFT_18

Amino acid counts for AGABI2DRAFT_48421:
A: 31
C: 13
D: 40
E: 34
F: 30
G: 33
H: 20
I: 33
K: 25
L: 57
M: 12
N: 32
P: 37
Q: 28
R: 41
S: 50
T: 33
V: 37
W: 9
Y: 13
----------------------------------------
Amino acid counts for AGABI2DRAFT_64658:
A: 18
C: 9
D: 15
E: 13
F: 9
G: 18
H: 9
I: 15
K: 21
L: 22
M: 6
N: 16
P: 26
Q: 24
R: 23
S: 30
T: 22
V: 21
W: 7
Y: 7
----------------------------------------
Amino acid counts for AGABI2DRAFT_115411:
A: 22
C: 10
D: 29
E: 20
F: 24
G: 24
H: 26
I: 27
K: 27
L: 47
M: 10
N: 10
P: 18
Q: 21
R: 19
S: 27
T: 19
V: 24
W: 12
Y: 20
----------------------------------------
Amino acid counts for AGABI2DRAFT_115412:
A: 16
C: 3
D: 9
E: 10
F: 12
G: 21
H: 10
I: 9
K: 7
L: 17
M: 4
N: 8
P: 19
Q: 16
R: 10
S: 28
T: 20
V: 10
W: 5
Y: 9
----------------------------------------
Amino acid counts for AGABI2DRAFT_63423:
A: 15
C: 13
D: 9
E: 1
F: 5
G: 7
H: 10
I: 4
K: 10
L: 3
M: 1
N: 5
P: 6
Q: 5
R: 13
S: 16
T: 6
V: 9
W: 5
Y: 1
----------------------------------------
Amino acid counts

Amino acid counts for AGABI2DRAFT_122285:
A: 27
C: 7
D: 29
E: 12
F: 12
G: 22
H: 24
I: 24
K: 18
L: 28
M: 8
N: 19
P: 37
Q: 31
R: 27
S: 41
T: 21
V: 24
W: 2
Y: 23
----------------------------------------
Amino acid counts for AGABI2DRAFT_195525:
A: 4
D: 11
E: 4
F: 3
G: 2
H: 1
I: 6
K: 1
L: 5
M: 3
N: 1
P: 5
Q: 5
R: 5
S: 5
T: 1
V: 5
W: 3
----------------------------------------
Amino acid counts for AGABI2DRAFT_228312:
A: 26
C: 7
D: 24
E: 19
F: 24
G: 19
H: 11
I: 25
K: 9
L: 59
M: 10
N: 10
P: 26
Q: 20
R: 30
S: 36
T: 19
V: 26
W: 9
Y: 9
----------------------------------------
Amino acid counts for AGABI2DRAFT_122287:
A: 36
C: 3
D: 47
E: 40
F: 27
G: 38
H: 18
I: 23
K: 31
L: 55
M: 16
N: 28
P: 27
Q: 23
R: 34
S: 42
T: 18
V: 38
W: 20
Y: 30
----------------------------------------
Amino acid counts for AGABI2DRAFT_54359:
A: 16
C: 4
D: 5
E: 14
F: 6
G: 15
H: 6
I: 11
K: 6
L: 15
M: 3
N: 8
P: 12
Q: 4
R: 13
S: 6
T: 9
V: 9
W: 4
Y: 6
----------------------------------------
Amino acid counts for AGABI2DRAFT_22

Amino acid counts for AGABI2DRAFT_122642:
A: 43
D: 46
E: 28
F: 28
G: 52
H: 34
I: 34
K: 28
L: 60
M: 14
N: 33
P: 77
Q: 33
R: 55
S: 101
T: 57
V: 49
W: 3
Y: 16
----------------------------------------
Amino acid counts for AGABI2DRAFT_139402:
A: 3
C: 3
D: 4
E: 2
F: 3
G: 5
H: 1
I: 7
L: 2
M: 1
N: 1
P: 1
Q: 1
R: 6
S: 3
T: 2
V: 8
Y: 1
----------------------------------------
Amino acid counts for AGABI2DRAFT_139403:
A: 10
C: 1
D: 3
E: 10
F: 4
G: 4
H: 3
I: 4
K: 4
L: 12
M: 5
N: 4
P: 4
Q: 3
R: 9
S: 7
T: 7
V: 7
Y: 6
----------------------------------------
Amino acid counts for AGABI2DRAFT_195761:
A: 59
C: 4
D: 21
E: 26
F: 30
G: 56
H: 1
I: 43
K: 26
L: 47
M: 13
N: 22
P: 16
Q: 13
R: 24
S: 35
T: 38
V: 42
W: 11
Y: 24
----------------------------------------
Amino acid counts for AGABI2DRAFT_195762:
A: 22
C: 5
D: 18
E: 20
F: 18
G: 25
H: 7
I: 14
K: 18
L: 38
M: 9
N: 19
P: 30
Q: 13
R: 20
S: 51
T: 26
V: 22
W: 5
Y: 16
----------------------------------------
Amino acid counts for AGABI2DRAFT_122647:
A: 21
C

In [4]:
# Q5

#!makeblastdb -help

# This command uses makeblastdb from the NCBI BLAST+ toolkit
# -in: input FASTA file 
# -dbtype prot: specifies that the database is of protein type
# -out: sets the name of the resulting BLAST database file

!makeblastdb -in /Users/shatakshishewale/Desktop/ncbi_dataset/ncbi_dataset/data/GCA_000300575.1/cds_translations.fasta -dbtype prot -out /Users/shatakshishewale/Desktop/ncbi_dataset/agaricus_prot_db

# Reference - https://www.ncbi.nlm.nih.gov/books/NBK52640/



Building a new DB, current time: 04/10/2025 17:53:36
New DB name:   /Users/shatakshishewale/Desktop/ncbi_dataset/agaricus_prot_db
New DB title:  /Users/shatakshishewale/Desktop/ncbi_dataset/ncbi_dataset/data/GCA_000300575.1/cds_translations.fasta
Sequence type: Protein
Deleted existing Protein BLAST database named /Users/shatakshishewale/Desktop/ncbi_dataset/agaricus_prot_db
Keep MBits: T
Maximum file size: 3000000000B
Adding sequences from FASTA; added 10448 sequences in 0.097641 seconds.




## Q6

### 1. Output Data Format
Illumina sequencing platforms initially generate output in the Binary Base Call (BCL) format. BCL files store per-cycle base calls and quality scores and are not directly usable for most downstream analyses. These are usually converted into the more analysis-friendly FASTQ format.

BCL: Raw binary files containing per-cycle sequencing information.

FASTQ: A text-based format combining nucleotide sequences and corresponding Phred quality scores. It’s the standard input for most downstream tools.

Line	Description
1	    Always begins with '@' and then information about the read
2	    The actual DNA sequence
3	    Always begins with a '+' and sometimes the same info in line 1
4	    Has a string of characters which represent the quality scores; must have same number of characters as line2

So for example in our data set, one complete read is:

$ head -n4 SRR098281.fastq 
@SRR098281.1 HWUSI-EAS1599_1:2:1:0:318 length=35
CNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNN
+SRR098281.1 HWUSI-EAS1599_1:2:1:0:318 length=35
#!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!


Reference - [File Formats for Illumina Sequencing](https://www.illumina.com/informatics/sequencing-data-analysis/sequence-file-formats.html) ; [Details on the FASTQ format
](https://jasonjwilliamsny.github.io/wrangling-genomics/00-readQC.html)


### 2. General Overview of Processing and QC
After sequencing, the pipeline typically follows these steps:

- BCL to FASTQ Conversion

Tools: bcl2fastq, BCL Convert, or DRAGEN

Converts .bcl to .fastq.gz per sample per read.


- Quality Control (QC)

Evaluate base quality, adapter contamination, GC content, duplication.

Tool: FastQC


- Trimming and Filtering

Remove low-quality reads, adapters, poly-N tails.

Tools: Trimmomatic, Cutadapt, or fastp


- Quality Re-Evaluation

Run FastQC again on trimmed reads to confirm improvements.


References - [Details on the FASTQ format](https://jasonjwilliamsny.github.io/wrangling-genomics/00-readQC.html) ; 
[BaRC](http://barcwiki.wi.mit.edu/wiki/SOPs/qc_shortReads) ; 
[NGS Data Analysis 101](https://www.youtube.com/live/V51MhSDX-YE?si=1Au-U76BZInJVpSZ)


### 3. Example command for quality and adapter trimming using Trimmomatic

```bash
java -jar trimmomatic-0.39.jar PE input_forward.fq.gz input_reverse.fq.gz output_forward_paired.fq.gz output_forward_unpaired.fq.gz output_reverse_paired.fq.gz output_reverse_unpaired.fq.gz ILLUMINACLIP:TruSeq3-PE.fa:2:30:10:2:True LEADING:3 TRAILING:3 MINLEN:36
```

This will perform the following:

Remove adapters (ILLUMINACLIP:TruSeq3-PE.fa:2:30:10)
Remove leading low quality or N bases (below quality 3) (LEADING:3)
Remove trailing low quality or N bases (below quality 3) (TRAILING:3)
Scan the read with a 4-base wide sliding window, cutting when the average quality per base drops below 15 (SLIDINGWINDOW:4:15)
Drop reads below the 36 bases long (MINLEN:36)

Reference - [Trimmomatic](http://www.usadellab.org/cms/?page=trimmomatic)

## Q7

### 1. Output Data Formats
Oxford Nanopore Technologies (ONT) sequencing data is typically stored in three main formats:

- POD5:
A new ONT-developed binary format that replaces the older .fast5 files.

Stores raw signal data from the nanopore.

Smaller file size, faster read/write access, and more computationally efficient than .fast5.

Used in basecalling and signal-level analysis.

- FASTQ:
Text-based format storing DNA/RNA sequences and their quality scores.
Used as input for downstream analysis such as alignment, assembly, and variant calling.

- BAM (optional):
Output when basecalled reads are aligned or when modified base calling is performed.

- sequencing_summary.txt:
A tab-delimited file containing metadata per read — e.g., read length, read ID, Q-score, and signal duration.

Reference - [Nanopore sequencing](https://nanoporetech.com/support/devices/PromethION-24-and-48/how-much-storage-space-is-required-for-promethion-sequencing-data) ; [Quality Control of Long Reads](https://www.youtube.com/watch?v=Zf0xX2CqkLw)


### 2. Overview of Processing and Quality Control
- Basecalling:
Converts raw FAST5 signal data to basecalled reads in FASTQ format.
Tool: Guppy.

- Demultiplexing (if barcoded):
Assigns reads to samples using barcodes.
Tool: guppy_barcoder.

- Quality Control:

Assess read length and quality distribution.

Filter low-quality reads (e.g., mean quality score < 7).

Remove short reads below a desired length.
Tools: NanoPlot, Filtlong.

References - [Guppy](https://nanoporetech.com/document/Guppy-protocol) ; [Fitlong](https://github.com/rrwick/Filtlong) ; [NanoPlot](https://github.com/wdecoster/NanoPlot)

- Adapter & Quality Trimming: Removes sequencing adapters and poor-quality bases.
Tool: Porechop (adapter trimming), or Filtlong (length & quality filtering).

Reference - [PoreChop](https://github.com/rrwick/Porechop)

### 3. Example Command for quality and adapter trimming using Porechop

```bash
porechop -i input_reads.fastq.gz -o output_reads.fastq.gz
```

What it does:
-i input_reads.fastq.gz: Specifies your raw input file from Nanopore sequencing in FASTQ format ;
-o output_reads.fastq.gz: The trimmed output FASTQ file where adapter sequences have been removed.

Reference - [PoreChop](https://github.com/rrwick/Porechop) (Quick usage examples section)

## Q8 

```bash
cat run1_R1.fastq.gz run2_R1.fastq.gz > pooled_R1.fastq.gz 
cat run1_R2.fastq.gz run2_R2.fastq.gz > pooled_R2.fastq.gz
```

Reference - [Biostars](https://www.biostars.org/p/9528574/)


## Q9

```bash
seqtk sample -s100 pooled_R1.fastq.gz 10000 > subsampled_R1.fastq
seqtk sample -s100 pooled_R2.fastq.gz 10000 > subsampled_R2.fastq
```

Reference - [seqtk](https://github.com/lh3/seqtk) (Subsample 10000 read pairs from two large paired FASTQ files example)

-------------------------

## Data science 
The Bioinformatics Scientist will work on a Linux system and will develop code in a collaborative and version-controlled way. This section is intended to evaluate your familiarity with working in a Linux environment and with collaborative code development. 

1. Your R1 and R2 sequence files from question 8 are on a server in the directory /z/data/. You would like to move them to a new subdirectory named 'illumina'. Please provide the commands necessary to create the 'illumina' directory within /z/data/ and to move the sequence files into this new directory.

2. What commands would you use to check the size of each of your sequence files and to count the number of lines and sequence reads in each?

3. You are collaborating with another scientist on a Python-based genomic assembly workflow that is within a GitLab repository called 'seq_repo'. In order to update the assembly script you need to pull the repository, make your updates in the script, then push your changes, and make a merge request. Please provide the commands you would use to pull, push, and create a merge request. 

4. Explain why you might want to use a test-driven development approach to programming, what are the pros and cons of test-driven development.

5. A strain engineer asks you to write a small python script that does read trimming (with _e.g._, [trimmomatic](https://github.com/timflutre/trimmomatic)) and assembly (with _e.g._ [spades](https://github.com/ablab/spades)). How would you go about this, and how would you make it as **easy as possible to maintain** for other bioinformatics scientists who might support it in the future? Please provide a small Python script that does this, along with notes about your coding strategy for making it maintainable and team-oriented.

## Q1

#### Create a new directory named 'illumina' inside /z/data/
```bash
mkdir /z/data/illumina
```

#### Move all R1 and R2 FASTQ files from /z/data/ into the new directory
```bash
mv /z/data/pooled_R1.fastq.gz /z/data/pooled_R2.fastq.gz /z/data/illumina/
```

#### Explanation:
mkdir /z/data/illumina — creates the new subdirectory called illumina.

mv ... /z/data/illumina/: moves the two pooled_R1 and pooled_R2 files into that folder.


Reference - [GNU Coreutils Manual](https://www.gnu.org/software/coreutils/manual/coreutils.html)

## Q2

#### Check the size of each sequence file:
```bash
du -h /z/data/illumina/pooled_R1.fastq.gz
du -h /z/data/illumina/pooled_R2.fastq.gz
```

#### Count number of lines in each file
```bash
zcat /z/data/illumina/pooled_R1.fastq.gz | wc -l
zcat /z/data/illumina/pooled_R2.fastq.gz | wc -l
```

#### Count the number of reads in each file:
```bash
zcat /z/data/illumina/pooled_R1.fastq.gz | wc -l | awk '{print $1/4 " reads"}'

zcat /z/data/illumina/pooled_R2.fastq.gz | wc -l | awk '{print $1/4 " reads"}'
```

Reference - [Bioinformatics Stack Exchange](https://bioinformatics.stackexchange.com/questions/20509/how-to-get-a-file-with-the-number-of-reads-for-several-fastq-gz-files)


## Q3

#### Step 1: clone and move into the local repo directory
```bash
git clone <copied URL>
cd seq_repo
```

#### Step 2: Make sure the local main branch is up to date
```bash
git checkout main
git pull origin main
```

#### Step 3: Create and switch to a new branch for the changes
```bash
git checkout -b update-feature
```

#### Step 4: Make your edits to the Python script (e.g., to code.py)

#### Step 5: Next commit your changes
```bash
git add code.py
git commit -m "Updated code.py script with new feature."
```

#### Step 6: Then push the branch to the GitLab remote
```bash
git push origin update-feature
```

#### Step 7: Create a merge request using glab mr
```bash
glab mr create --source update-feature --target main --description "New feature added"
```


Reference - [GitLab documentation - glab mr](https://gitlab.com/gitlab-org/cli/-/tree/main/docs/source/mr) ; [GitLab documentation](https://docs.gitlab.com/topics/git/clone/)


## Q4

Test-Driven Development (TDD) is a software development approach where you write tests before writing the actual code. This helps you clearly understand what the code is supposed to do.

- Pros:

Fewer bugs: Since tests are written first, issues are caught early.

Better design: Code becomes more modular and easier to read.

Confidence in code changes: You can quickly check if new updates break anything.

- Cons:

Takes more time at the start: Writing tests before code can slow initial progress.

Not ideal for UI-heavy tasks: It’s harder to write tests for things like user interfaces.


Reference - [Test sigma](https://testsigma.com/blog/test-driven-development-testsigma/) ; [The Testing Academy](https://www.youtube.com/watch?v=h26wrTxF94k&t=7s)


## Q5

To support collaboration and maintainability, I wrote a modular Python script that integrates read trimming (via Trimmomatic) and genome assembly (via SPAdes). I’ve used clearly named functions, printed progress updates, and included docstrings to explain usage. This structure allows future collaborators to easily adapt the script to their specific needs (e.g., swap tools or change parameters).

```python

import subprocess
import os

def run_trimmomatic(forward_in, reverse_in, forward_out, reverse_out, trimmomatic_jar, adapter_file):
    """
    Runs Trimmomatic to trim Illumina reads.

    Parameters:
    forward_in (str): Path to forward reads input file (R1)
    reverse_in (str): Path to reverse reads input file (R2)
    forward_out (str): Path for trimmed forward reads output (R1 paired)
    reverse_out (str): Path for trimmed reverse reads output (R2 paired)
    trimmomatic_jar (str): Path to Trimmomatic .jar file
    adapter_file (str): Path to adapter FASTA file (e.g., TruSeq3-PE.fa)
    """
    cmd = [
        "java", "-jar", trimmomatic_jar, "PE",
        "-phred33", forward_in, reverse_in,
        forward_out, "unpaired_R1.fastq.gz",
        reverse_out, "unpaired_R2.fastq.gz",
        f"ILLUMINACLIP:{adapter_file}:2:30:10",
        "LEADING:3", "TRAILING:3", "SLIDINGWINDOW:4:15", "MINLEN:36"
    ]
    print("Running Trimmomatic...")
    subprocess.run(cmd, check=True)
    print("Trimming complete.")

def run_spades(forward_trimmed, reverse_trimmed, output_dir):
    """
    Runs SPAdes genome assembler on paired trimmed reads.

    Parameters:
    forward_trimmed (str): Path to trimmed forward reads
    reverse_trimmed (str): Path to trimmed reverse reads
    output_dir (str): Output directory for assembly
    """
    cmd = [
        "spades.py",
        "-1", forward_trimmed,
        "-2", reverse_trimmed,
        "-o", output_dir
    ]
    print("Running SPAdes...")
    subprocess.run(cmd, check=True)
    print(f"Assembly complete. Results saved to: {output_dir}")
    
```

Reference - [spades](https://github.com/ablab/spades) ; [trimmomatic](https://github.com/timflutre/trimmomatic)